In [1]:
import gc
from glob import glob
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from pathlib import Path
import time
from collections import OrderedDict
from tqdm import tqdm

import category_encoders as ce
import catboost
from sklearn import metrics

import sys
sys.path.append("../utils")
from metrics import compute_recall_at4, compute_normalized_gini, compute_amex_metric
#from messaging import send_message

pd.set_option('display.max_columns', None)

In [2]:
catboost.__version__

'1.0.6'

In [3]:
# metrics in catboost format
class AmexMetric:
    
    def is_max_optimal(self):
        return True

    def evaluate(self, approxes, target, weight):    
        assert len(approxes) == 1
        assert len(target) == len(approxes[0])
        scores = approxes[0]
        target = target
        return compute_amex_metric(target, scores), 1.

    def get_final_error(self, error, weight):
        return error

class RecallAt4:
    
    def is_max_optimal(self):
        return True

    def evaluate(self, approxes, target, weight):
        assert len(approxes) == 1
        assert len(target) == len(approxes[0])
        scores = np.array(approxes[0])
        target = np.array(target)                                   
        return compute_recall_at4(target, scores), 1.

    def get_final_error(self, error, weight):
        return error

class NormGini:
    
    def is_max_optimal(self):
        return True

    def evaluate(self, approxes, target, weight):
        assert len(approxes) == 1
        assert len(target) == len(approxes[0])
        scores = np.array(approxes[0])
        target = np.array(target)                   
        return compute_normalized_gini(target, scores), 1.

    def get_final_error(self, error, weight):
        return error

In [4]:
# CONFIG PARAMS
N_REPEATS = 1
DATASET_VERSION = "05"

In [5]:
OUT_PATH = Path(f"../data/feat-selection")

if not OUT_PATH.exists():
    OUT_PATH.mkdir(parents=True, exist_ok=True)

***
## load and prepare data

In [6]:
train = pd.read_parquet(f"../data/processed/dsv{DATASET_VERSION}/train.parquet")
train_labels = pd.read_csv("../data/raw/train_labels.csv", index_col="customer_ID")

In [7]:
train.info()

<class 'pandas.core.frame.DataFrame'>
Index: 458913 entries, 0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fbac11a8ed792feb62a to fffff1d38b785cef84adeace64f8f83db3a0c31e8d92eaba8b115f71cab04681
Columns: 8135 entries, P_2_mean_nan to S_2_max_gap
dtypes: float32(5473), int16(49), int8(2613)
memory usage: 10.5+ GB


In [8]:
input_feats = train.columns.tolist()
#categ_feats = [
#    'B_30_first', 'B_38_first', 'D_114_first', 'D_116_first', 'D_117_first', 
#    'D_120_first', 'D_126_first', 'D_63_first', 'D_64_first', 'D_66_first', 'D_68_first',
#    'B_30_last', 'B_38_last', 'D_114_last', 'D_116_last', 'D_117_last', 
#    'D_120_last', 'D_126_last', 'D_63_last', 'D_64_last', 'D_66_last', 'D_68_last',
#]
len(input_feats)

8135

In [9]:
train = pd.merge(train, train_labels, how="inner", left_index=True, right_index=True)
del train_labels
gc.collect()

0

***
## model training

In [10]:
model_params = {
    'eval_metric':AmexMetric(),
    'learning_rate': 0.05,
    'nan_mode':'Min',
    'random_seed': 2112,
    'auto_class_weights': None,
    'bootstrap_type': 'Bernoulli',
    'depth': 5,
    'rsm': 0.2,
    'iterations': 3900,
    'l2_leaf_reg': 8.017281499631434,
    'min_data_in_leaf': 1600,
    'random_strength': 7.69963242351621,
    'subsample': 0.8500000000000001,
    # early stopping
    'early_stopping_rounds':300,
    'use_best_model': True,
 }

In [11]:
def train_models(dataframe: pd.DataFrame, n_folds: int = 5,) -> tuple:
    
    models = list()
    oof_dfs = list()
    
    for fold in range(n_folds):
        
        print(f" training model {fold+1}/{n_folds} ".center(100, "#"))
        
        train_df = dataframe.query("fold != @fold").copy()
        valid_df = dataframe.query("fold == @fold").copy()
                
        train_dset = catboost.Pool(
            data=train_df.loc[:,input_feats],
            label=train_df.loc[:,"target"].values,
            #cat_features=categ_feats,
        )
        valid_dset = catboost.Pool(
            data=valid_df.loc[:,input_feats],
            label=valid_df.loc[:,"target"].values,
            #cat_features=categ_feats,
        )
        
        model = catboost.CatBoostClassifier(**model_params)
        model.fit(
            train_dset,
            eval_set=valid_dset,
            verbose=50,
        )
                    
        valid_df.loc[:,"pred"] = model.predict(valid_dset, prediction_type="Probability")[:,1]
        
        models.append(model)
        oof_dfs.append(valid_df)
        del train_df,train_dset,valid_dset
        gc.collect()
    
    return models,oof_dfs

In [12]:
%%time 

all_models = list()
all_oof_dfs = list()

for repetition in range(N_REPEATS):
    print(f" repeated cross-validation step: {repetition+1}/{N_REPEATS} ".center(100, "#"))

    folds = pd.read_csv(f'../data/processed/cv{repetition}.csv', index_col="customer_ID")
    _train = pd.merge(train, folds, how="inner", left_index=True, right_index=True).reset_index(drop=True)
    
    tic = time.time()
    models,oof_dfs = train_models(_train)
    tac = time.time()
    print(f"Training time: {(tac-tic)/60} min.")
              
    all_models.extend(models)
    all_oof_dfs.extend(oof_dfs)
              
    del _train, folds; gc.collect()

############################### repeated cross-validation step: 1/1 ################################
######################################## training model 1/5 ########################################
0:	learn: 0.6149372	test: 0.6220512	best: 0.6220512 (0)	total: 3.26s	remaining: 3h 31m 38s
50:	learn: 0.7465300	test: 0.7519887	best: 0.7519887 (50)	total: 39.6s	remaining: 49m 50s
100:	learn: 0.7582866	test: 0.7630486	best: 0.7630486 (100)	total: 1m 15s	remaining: 47m 27s
150:	learn: 0.7635784	test: 0.7690186	best: 0.7691370 (149)	total: 1m 52s	remaining: 46m 37s
200:	learn: 0.7677412	test: 0.7720988	best: 0.7720988 (200)	total: 2m 29s	remaining: 45m 54s
250:	learn: 0.7716505	test: 0.7748670	best: 0.7749875 (242)	total: 3m 5s	remaining: 45m 2s
300:	learn: 0.7768931	test: 0.7794865	best: 0.7794865 (300)	total: 3m 42s	remaining: 44m 24s
350:	learn: 0.7816870	test: 0.7833699	best: 0.7833699 (350)	total: 4m 20s	remaining: 43m 51s
400:	learn: 0.7852150	test: 0.7865174	best: 0.7866623 (396)	t

***
## computes LFC (loss function change)

In [13]:
outputs = list()

for model,oof_df in zip(all_models,all_oof_dfs):
    oof_dset = catboost.Pool(
        data = oof_df.loc[:,input_feats],
        label = oof_df.loc[:,"target"].values,
    )
    out = model.get_feature_importance(
        data = oof_dset,
        type = "LossFunctionChange",
        verbose=True,
    )
    outputs.append(out)

Used Logloss metric for fstr calculation
Selected 91783 documents from 91783 for LossFunctionChange calculation.
Used Logloss metric for fstr calculation
Started LossFunctionChange calculation
278/91783 Process documents	passed time: 189ms	remaining time: 1m 2s
556/91783 Process documents	passed time: 379ms	remaining time: 1m 2s
834/91783 Process documents	passed time: 569ms	remaining time: 1m 2s
1112/91783 Process documents	passed time: 756ms	remaining time: 1m 1s
1390/91783 Process documents	passed time: 944ms	remaining time: 1m 1s
1668/91783 Process documents	passed time: 1.13s	remaining time: 1m 1s
1946/91783 Process documents	passed time: 1.32s	remaining time: 1m
2224/91783 Process documents	passed time: 1.51s	remaining time: 1m
2502/91783 Process documents	passed time: 1.71s	remaining time: 1m
2780/91783 Process documents	passed time: 1.89s	remaining time: 1m
3058/91783 Process documents	passed time: 2.08s	remaining time: 1m
3336/91783 Process documents	passed time: 2.27s	remaini

In [14]:
result_lfc = pd.DataFrame(outputs, columns=input_feats)
result_lfc.to_csv(OUT_PATH/"catb-lfc.csv", index=False)
result_lfc

P_2_mean_nan   P_2_sum_nan  D_39_mean_nan  D_39_sum_nan  B_1_mean_nan  \
0      0.000000  3.526920e-06            0.0           0.0           0.0   
1      0.000000  0.000000e+00            0.0           0.0           0.0   
2     -0.000002 -4.346214e-06            0.0           0.0           0.0   
3      0.000000 -1.116270e-06            0.0           0.0           0.0   
4     -0.000002  9.617163e-08            0.0           0.0           0.0   

   B_1_sum_nan  B_2_mean_nan   B_2_sum_nan  R_1_mean_nan  R_1_sum_nan  \
0          0.0           0.0 -7.763870e-07           0.0          0.0   
1          0.0           0.0  0.000000e+00           0.0          0.0   
2          0.0           0.0  0.000000e+00           0.0          0.0   
3          0.0           0.0  0.000000e+00           0.0          0.0   
4          0.0           0.0 -2.930204e-07           0.0          0.0   

   S_3_mean_nan  S_3_sum_nan  D_41_mean_nan  D_41_sum_nan  B_3_mean_nan  \
0  4.361466e-07     0.000000            0.0           0.0           0.0   
1  4.057998e-06     0.000000            0.0           0.0           0.0   
2  0.000000e+00     0.000002            0.0           0.0           0.0   
3  0.000000e+00     0.000000            0.0           0.0           0.0   
4  3.317701e-07    -0.000001            0.0           0.0           0.0   

   B_3_sum_nan  D_42_mean_nan  D_42_sum_nan  D_43_mean_nan  D_43_sum_nan  \
0          0.0   0.000000e+00      0.000000       0.000000      0.000002   
1          0.0   0.000000e+00      0.000032       0.000005      0.000000   
2          0.0  -7.259634e-08      0.000000      -0.000001     -0.000005   
3          0.0   3.811224e-06      0.000002       0.000000      0.000002   
4          0.0   0.000000e+00      0.000006       0.000001      0.000001   

   D_44_mean_nan  D_44_sum_nan  B_4_mean_nan  B_4_sum_nan  D_45_mean_nan  \
0            0.0           0.0           0.0          0.0            0.0   
1            0.0           0.0           0.0          0.0            0.0   
2            0.0           0.0           0.0          0.0            0.0   
3            0.0           0.0           0.0          0.0            0.0   
4            0.0           0.0           0.0          0.0            0.0   

   D_45_sum_nan  B_5_mean_nan  B_5_sum_nan  R_2_mean_nan  R_2_sum_nan  \
0           0.0           0.0          0.0           0.0          0.0   
1           0.0           0.0          0.0           0.0          0.0   
2           0.0           0.0          0.0           0.0          0.0   
3           0.0           0.0          0.0           0.0          0.0   
4           0.0           0.0          0.0           0.0          0.0   

   D_46_mean_nan  D_46_sum_nan  D_47_mean_nan  D_47_sum_nan  D_48_mean_nan  \
0  -5.664608e-07  0.000000e+00            0.0           0.0   6.719330e-07   
1   0.000000e+00  0.000000e+00            0.0           0.0   4.619438e-06   
2   5.544907e-07  0.000000e+00            0.0           0.0   0.000000e+00   
3   9.814668e-07  0.000000e+00            0.0           0.0   0.000000e+00   
4   2.178459e-07 -1.577739e-07            0.0           0.0   0.000000e+00   

   D_48_sum_nan  D_49_mean_nan  D_49_sum_nan  B_6_mean_nan  B_6_sum_nan  \
0      0.000000            0.0           0.0           0.0          0.0   
1      0.000000            0.0           0.0           0.0          0.0   
2      0.000000            0.0           0.0           0.0          0.0   
3      0.000002            0.0           0.0           0.0          0.0   
4      0.000000            0.0           0.0           0.0          0.0   

   B_7_mean_nan  B_7_sum_nan  B_8_mean_nan   B_8_sum_nan  D_50_mean_nan  \
0           0.0          0.0      0.000002 -9.638058e-07   2.206500e-06   
1           0.0          0.0     -0.000001 -1.499442e-07  -8.948356e-06   
2           0.0          0.0      0.000000  0.000000e+00   2.787098e-07   
3           0.0          0.0      0.000000  0.000000e+00   0.000000e+00   
4       

***
## computes SHAP

In [15]:
outputs = list()

for model,oof_df in zip(all_models,all_oof_dfs):  
    oof_dset = catboost.Pool(
        data = oof_df.loc[:,input_feats],
        label = oof_df.loc[:,"target"].values,
    )
    out = model.get_feature_importance(
        data = oof_dset,
        type = "ShapValues",
        verbose=True,
    )
    outputs.append(np.mean(np.abs(out[:,:-1]), axis=0))

Processing trees...
128/2142 trees processed	passed time: 9.66ms	remaining time: 152ms
256/2142 trees processed	passed time: 17ms	remaining time: 125ms
384/2142 trees processed	passed time: 24.6ms	remaining time: 113ms
512/2142 trees processed	passed time: 32.5ms	remaining time: 103ms
640/2142 trees processed	passed time: 40.5ms	remaining time: 95.2ms
768/2142 trees processed	passed time: 48.1ms	remaining time: 86ms
896/2142 trees processed	passed time: 55.4ms	remaining time: 77.1ms
1024/2142 trees processed	passed time: 62.9ms	remaining time: 68.6ms
1152/2142 trees processed	passed time: 70ms	remaining time: 60.1ms
1280/2142 trees processed	passed time: 76.8ms	remaining time: 51.7ms
1408/2142 trees processed	passed time: 84ms	remaining time: 43.8ms
1536/2142 trees processed	passed time: 90.9ms	remaining time: 35.9ms
1664/2142 trees processed	passed time: 98ms	remaining time: 28.2ms
1792/2142 trees processed	passed time: 105ms	remaining time: 20.5ms
1920/2142 trees processed	passed tim

In [16]:
results_shap = pd.DataFrame(outputs, columns=input_feats)
results_shap.to_csv(OUT_PATH/"catb-shap.csv", index=False)
results_shap

P_2_mean_nan  P_2_sum_nan  D_39_mean_nan  D_39_sum_nan  B_1_mean_nan  \
0      0.000000     0.000233            0.0           0.0           0.0   
1      0.000000     0.000000            0.0           0.0           0.0   
2      0.000242     0.000781            0.0           0.0           0.0   
3      0.000000     0.000228            0.0           0.0           0.0   
4      0.000505     0.000132            0.0           0.0           0.0   

   B_1_sum_nan  B_2_mean_nan  B_2_sum_nan  R_1_mean_nan  R_1_sum_nan  \
0          0.0           0.0     0.000119           0.0          0.0   
1          0.0           0.0     0.000000           0.0          0.0   
2          0.0           0.0     0.000000           0.0          0.0   
3          0.0           0.0     0.000000           0.0          0.0   
4          0.0           0.0     0.000078           0.0          0.0   

   S_3_mean_nan  S_3_sum_nan  D_41_mean_nan  D_41_sum_nan  B_3_mean_nan  \
0      0.000254     0.000000            0.0           0.0           0.0   
1      0.001382     0.000000            0.0           0.0           0.0   
2      0.000000     0.000855            0.0           0.0           0.0   
3      0.000000     0.000000            0.0           0.0           0.0   
4      0.000529     0.000433            0.0           0.0           0.0   

   B_3_sum_nan  D_42_mean_nan  D_42_sum_nan  D_43_mean_nan  D_43_sum_nan  \
0          0.0       0.000000      0.000000       0.000000      0.000737   
1          0.0       0.000000      0.021167       0.002487      0.000000   
2          0.0       0.000560      0.000000       0.002877      0.003294   
3          0.0       0.001298      0.001376       0.000000      0.002251   
4          0.0       0.000000      0.004335       0.000576      0.001022   

   D_44_mean_nan  D_44_sum_nan  B_4_mean_nan  B_4_sum_nan  D_45_mean_nan  \
0            0.0           0.0           0.0          0.0            0.0   
1            0.0           0.0           0.0          0.0            0.0   
2            0.0           0.0           0.0          0.0            0.0   
3            0.0           0.0           0.0          0.0            0.0   
4            0.0           0.0           0.0          0.0            0.0   

   D_45_sum_nan  B_5_mean_nan  B_5_sum_nan  R_2_mean_nan  R_2_sum_nan  \
0           0.0           0.0          0.0           0.0          0.0   
1           0.0           0.0          0.0           0.0          0.0   
2           0.0           0.0          0.0           0.0          0.0   
3           0.0           0.0          0.0           0.0          0.0   
4           0.0           0.0          0.0           0.0          0.0   

   D_46_mean_nan  D_46_sum_nan  D_47_mean_nan  D_47_sum_nan  D_48_mean_nan  \
0       0.000377      0.000000            0.0           0.0       0.000481   
1       0.000000      0.000000            0.0           0.0       0.001223   
2       0.000404      0.000000            0.0           0.0       0.000000   
3       0.001490      0.000000            0.0           0.0       0.000000   
4       0.000689      0.000623            0.0           0.0       0.000000   

   D_48_sum_nan  D_49_mean_nan  D_49_sum_nan  B_6_mean_nan  B_6_sum_nan  \
0      0.000000            0.0           0.0           0.0          0.0   
1      0.000000            0.0           0.0           0.0          0.0   
2      0.000000            0.0           0.0           0.0          0.0   
3      0.000803            0.0           0.0           0.0          0.0   
4      0.000000            0.0           0.0           0.0          0.0   

   B_7_mean_nan  B_7_sum_nan  B_8_mean_nan  B_8_sum_nan  D_50_mean_nan  \
0           0.0          0.0      0.000166     0.000159       0.013173   
1           0.0          0.0      0.000216     0.000050       0.012382   
2           0.0          0.0      0.000000     0.000000       0.007402   
3           0.0          0.0      0.000000     0.000000       0.000000   
4           0.0          

***
## computes PFI

In [17]:
def compute_pfi(
        model:catboost.core.CatBoostClassifier,
        dataframe:pd.DataFrame, 
        features:list, 
        target:str
    ):
    dataframe = dataframe.copy()
    
    # calculates base score
    preds = model.predict(dataframe[features], prediction_type="Probability")[:,1]
    target = dataframe[target].values
    BASE_SCORE = compute_amex_metric(target, preds)

    output = OrderedDict()
    output["base_score"] = BASE_SCORE

    # calculates pfi for each feature
    for col in tqdm(features):
        raw_values = dataframe[col].copy()
        index = np.random.permutation(dataframe.index.values)
        dataframe[col] = dataframe.loc[index, col].values
        preds = model.predict(dataframe[features], prediction_type="Probability")[:,1]
        score = compute_amex_metric(target, preds)
        pfi = (BASE_SCORE - score)
        output[col] = pfi
        # rollback the permutation
        dataframe[col] = raw_values
        del raw_values
        
    return output

In [18]:
outputs = list()

for model,oof_df in zip(all_models,all_oof_dfs):
    out = compute_pfi(
        model=model,
        dataframe=oof_df,
        features=input_feats,
        target="target",
    )
    outputs.append(out)

100%|██████████████████████████████████████████████████| 8135/8135 [3:33:28<00:00,  1.57s/it]


In [19]:
result_pfi = pd.DataFrame(outputs)
result_pfi.to_csv(OUT_PATH/"catb-pfi.csv", index=False)
result_pfi

base_score  P_2_mean_nan   P_2_sum_nan  D_39_mean_nan  D_39_sum_nan  \
0    0.798064      0.000000  1.504626e-04            0.0           0.0   
1    0.794462      0.000000  0.000000e+00            0.0           0.0   
2    0.789837      0.000021 -2.771471e-07            0.0           0.0   
3    0.788120      0.000000 -6.867104e-07            0.0           0.0   
4    0.797813     -0.000042  2.225932e-06            0.0           0.0   

   B_1_mean_nan  B_1_sum_nan  B_2_mean_nan   B_2_sum_nan  R_1_mean_nan  \
0           0.0          0.0           0.0 -5.264559e-07           0.0   
1           0.0          0.0           0.0  0.000000e+00           0.0   
2           0.0          0.0           0.0  0.000000e+00           0.0   
3           0.0          0.0           0.0  0.000000e+00           0.0   
4           0.0          0.0           0.0 -2.172791e-05           0.0   

   R_1_sum_nan  S_3_mean_nan  S_3_sum_nan  D_41_mean_nan  D_41_sum_nan  \
0          0.0      0.000128     0.000000            0.0           0.0   
1          0.0     -0.000105     0.000000            0.0           0.0   
2          0.0      0.000000    -0.000104            0.0           0.0   
3          0.0      0.000000     0.000000            0.0           0.0   
4          0.0      0.000021     0.000042            0.0           0.0   

   B_3_mean_nan  B_3_sum_nan  D_42_mean_nan  D_42_sum_nan  D_43_mean_nan  \
0           0.0          0.0       0.000000      0.000000       0.000000   
1           0.0          0.0       0.000000      0.000456       0.000106   
2           0.0          0.0       0.000126      0.000000       0.000129   
3           0.0          0.0       0.000128      0.000274       0.000000   
4           0.0          0.0       0.000000      0.000196       0.000064   

   D_43_sum_nan  D_44_mean_nan  D_44_sum_nan  B_4_mean_nan  B_4_sum_nan  \
0      0.000148            0.0           0.0           0.0          0.0   
1      0.000000            0.0           0.0           0.0          0.0   
2      0.000167            0.0           0.0           0.0          0.0   
3      0.000126            0.0           0.0           0.0          0.0   
4     -0.000042            0.0           0.0           0.0          0.0   

   D_45_mean_nan  D_45_sum_nan  B_5_mean_nan  B_5_sum_nan  R_2_mean_nan  \
0            0.0           0.0           0.0          0.0           0.0   
1            0.0           0.0           0.0          0.0           0.0   
2            0.0           0.0           0.0          0.0           0.0   
3            0.0           0.0           0.0          0.0           0.0   
4            0.0           0.0           0.0          0.0           0.0   

   R_2_sum_nan  D_46_mean_nan  D_46_sum_nan  D_47_mean_nan  D_47_sum_nan  \
0          0.0       0.000146      0.000000            0.0           0.0   
1          0.0       0.000000      0.000000            0.0           0.0   
2          0.0       0.000021      0.000000            0.0           0.0   
3          0.0       0.000211      0.000000            0.0           0.0   
4          0.0       0.000021      0.000021            0.0           0.0   

   D_48_mean_nan  D_48_sum_nan  D_49_mean_nan  D_49_sum_nan  B_6_mean_nan  \
0       0.000151  0.000000e+00            0.0           0.0           0.0   
1       0.000068  0.000000e+00            0.0           0.0           0.0   
2       0.000000  0.000000e+00            0.0           0.0           0.0   
3       0.000000  2.629297e-07            0.0           0.0           0.0   
4       0.000000  0.000000e+00            0.0           0.0           0.0   

   B_6_sum_nan  B_7_mean_nan  B_7_sum_nan  B_8_mean_nan  B_8_sum_nan  \
0          0.0           0.0          0.0  4.343791e-05     0.000042   
1          0.0           0.0          0.0  5.456334e-07    -0.000021   
2          0.0           0.0          0.0  0.000000e+00     0.000000   
3          0.0           0.0          0.0  0.000000e+00     0.000000   
4          0.0           0.0 

***